Dependencies

In [1]:
pip install pillow datasets pandas pypng uuid


  Preparing metadata (setup.py) ... done
  DEPRECATION: uuid is being installed using the legacy 'setup.py install' method, because it does not have a 'pyproject.toml' and the 'wheel' package is not installed. pip 23.1 will enforce this behaviour change. A possible replacement is to enable the '--use-pep517' option. Discussion can be found at https://github.com/pypa/pip/issues/8559
  Running setup.py install for uuid ... done

[notice] A new release of pip is available: 23.0.1 -> 24.1.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


Preproccessing

In [2]:
import os
import uuid
import shutil

def rename_and_move_images(source_dir, target_dir):
    # Create the target directory if it doesn't exist
    os.makedirs(target_dir, exist_ok=True)

    # List of common image file extensions
    image_extensions = ('.jpg', '.jpeg', '.png', '.gif', '.bmp', '.tiff')

    # Walk through the source directory and its subdirectories
    for root, dirs, files in os.walk(source_dir):
        for file in files:
            # Check if the file has an image extension
            if file.lower().endswith(image_extensions):
                # Generate a new filename with UUID
                new_filename = str(uuid.uuid4()) + os.path.splitext(file)[1]
                
                # Construct full file paths
                old_path = os.path.join(root, file)
                new_path = os.path.join(target_dir, new_filename)
                
                # Move and rename the file
                shutil.move(old_path, new_path)
                print(f"Moved and renamed: {old_path} -> {new_path}")

# Usage
source_directory = "images"
target_directory = "train"

rename_and_move_images(source_directory, target_directory)

Moved and renamed: images/japanese streetscapes_00125_.png -> train/63d84ebd-201f-45cc-8cfc-35e1ecbac724.png
Moved and renamed: images/japanese streetscapes_00430_.png -> train/a4bf9402-0c76-44cc-9ee6-3e613539c393.png
Moved and renamed: images/japanese streetscapes_00060_.png -> train/71ca8683-9822-4426-b338-a99e298dbbf5.png
Moved and renamed: images/japanese streetscapes_00349_.png -> train/bbd6507a-deff-49cc-8605-2b1ff93c028f.png
Moved and renamed: images/japanese streetscapes_00172_.png -> train/f32ef431-5ecc-4fbd-8983-db4cd7d9f778.png
Moved and renamed: images/japanese streetscapes_00488_.png -> train/fd4988e7-37d3-46cc-9c4f-864cf3f7dd47.png
Moved and renamed: images/japanese streetscapes_00037_.png -> train/efa318eb-fd21-4f1b-8878-356559aff973.png
Moved and renamed: images/japanese streetscapes_00467_.png -> train/8bc842d3-565d-4a0a-b612-a9a175e0cdff.png
Moved and renamed: images/japanese streetscapes_00164_.png -> train/0e3397d3-5d98-48a5-a19a-92498dddcff7.png
Moved and renamed: 

Extract the Metadata

In [3]:
import os
import json
import png
import pandas as pd

# Directory containing images
image_dir = 'train'
metadata_list = []

# Function to extract the JSON data from the tEXt chunk in PNG images
def extract_metadata_from_png(image_path):
    with open(image_path, 'rb') as f:
        reader = png.Reader(file=f)
        chunks = reader.chunks()
        for chunk_type, chunk_data in chunks:
            if chunk_type == b'tEXt':
                # Convert bytes to string
                chunk_text = chunk_data.decode('latin1')
                if 'prompt' in chunk_text:
                    try:
                        # Extract JSON string after "prompt\0"
                        json_str = chunk_text.split('prompt\0', 1)[1]
                        json_data = json.loads(json_str)
                        inputs = json_data.get('3', {}).get('inputs', {})
                        seed = inputs.get('seed', 'N/A')
                        positive_prompt = json_data.get('6', {}).get('inputs', {}).get('text', 'N/A')
                        negative_prompt = json_data.get('7', {}).get('inputs', {}).get('text', 'N/A')
                        model = json_data.get('4', {}).get('inputs', {}).get('ckpt_name', 'N/A')
                        steps = inputs.get('steps', 'N/A')
                        cfg = inputs.get('cfg', 'N/A')
                        sampler_name = inputs.get('sampler_name', 'N/A')
                        scheduler = inputs.get('scheduler', 'N/A')
                        denoise = inputs.get('denoise', 'N/A')
                        return {
                            'seed': seed,
                            'positive_prompt': positive_prompt,
                            'negative_prompt': negative_prompt,
                            'model': model,
                            'steps': steps,
                            'cfg': cfg,
                            'sampler_name': sampler_name,
                            'scheduler': scheduler,
                            'denoise': denoise
                        }
                    except json.JSONDecodeError:
                        pass
    return {}

# Loop through all images in the directory
for file_name in os.listdir(image_dir):
    if file_name.endswith('.png'):
        image_path = os.path.join(image_dir, file_name)
        metadata = extract_metadata_from_png(image_path)
        metadata['file_name'] = file_name
        metadata_list.append(metadata)

# Convert metadata to DataFrame
metadata_df = pd.DataFrame(metadata_list)

# Ensure 'file_name' is the first column
columns_order = ['file_name', 'seed', 'positive_prompt', 'negative_prompt', 'model', 'steps', 'cfg', 'sampler_name', 'scheduler', 'denoise']
metadata_df = metadata_df[columns_order]

# Save metadata to a CSV file
metadata_csv_path = 'train/metadata.csv'
metadata_df.to_csv(metadata_csv_path, index=False)

print("Metadata extraction complete. Metadata saved to:", metadata_csv_path)




Metadata extraction complete. Metadata saved to: train/metadata.csv
